# Estructura de la materia 3
## Trabajo final: DFT de Helio en GS
### PARTE A: Hartree-Fock con omisión de electron self-interaction
Mendez, Alejandra

In [1]:
%matplotlib inline

In [2]:
from numpy import sqrt, exp, linspace, zeros, identity, array, diag, c_, pi
from math import factorial
from numpy.linalg import eigh
from scipy.integrate import quad
from scipy.special import hyp1f1
from matplotlib.pyplot import plot, axis, title, xlabel, ylabel, show,\
                              legend, subplot

In [3]:
# Normalización de las funciones 
def Normalizate(U,x):
    h = x[1]-x[0] # assume uniformly spaced points
    n = len(x)
    for j in range(0,n-1):
        suma = 0.0
        for i in range(0,n-1):
             suma = suma + U[i,j]**2
        suma = suma*h 
        rnorm = 1/sqrt(suma)
#       Normalization
        rsign = 1
        if U[1,j] < 0:
            rsign = -1
        rnorm = rnorm * rsign
        for i in range(0,n):
            U[i,j] = U[i,j]*rnorm
    return  U

In [4]:
def Laplacian(x):
    h = x[1]-x[0] # assume uniformly spaced points
    n = len(x)
    M = -2*identity(n,'d')
    for i in range(1,n):
        M[i,i-1] = M[i-1,i] = 1
    return M/h**2

In [5]:
# Defino las dimensiones de los arrays a utilizar
nsize = 2000
rmax = 10.0
h = rmax/nsize
rmin = h

In [6]:
print(h)

0.005


In [7]:
# Defino las matrices y vectores necesarios
r = linspace(rmin,rmax,nsize)
T = array([nsize,nsize])
Vs = array([nsize,nsize])
U = zeros([nsize,nsize])
H = array([nsize,nsize])
E = array([nsize])

In [8]:
Upp = zeros(nsize)
Up = zeros(nsize)
Zh = zeros(nsize)
Vh = zeros(nsize)
den = zeros(nsize)

In [7]:
# Defino el sistema a resolver: Helio en el estado fundamental
Z = 2
l = 0

La ecuación de Kohn-Sham está dada por 
\begin{equation}
  \left[-\frac{1}{2}\nabla^2 + V_{\mathrm{s}}\left(n|\mathbf{r}\right)\right] \phi_i = \epsilon_i \phi_i
\end{equation}

donde

\begin{equation}
  V_{\mathrm{s}}(n|\mathbf{r}) = V_{\mathrm{ext}}(r) + V_{\mathrm{H}}^*(n|\mathbf{r})
\end{equation}

El potencial de Hartree en el esquema no-self interaction del Helio está dado por:

\begin{equation}
   V_{\mathrm{H}}^*(n|\mathbf{r}) = \int{d\mathbf{r}\,\frac{n_i(\mathbf{r}')}{|\mathbf{r}-\mathbf{r}'|}}
\end{equation}

donde $n_i(r)=\left|\phi_i\right|^2$ es la densidad single orbital.

\begin{equation}
   \quad \Rightarrow \quad 
   \nabla^2 V_{\mathrm{H}}^*(n|\mathbf{r}) = -4\pi \, n_{\mathrm{s}}(\mathbf{r})
\end{equation}

Debido a la simetría radial de la densidad,

\begin{equation}
  Z_{\mathrm{H}}(r) = r V_{\mathrm{H}}^*(r) 
   \quad \Rightarrow \quad 
   \frac{d^2 Z_{\mathrm{H}}(r)}{dr^2} = -4\pi \, r\,n_{\mathrm{s}}(r)
\end{equation}

Resuelvo usando el algoritmo de Verlet, e imponiendo dos condiciones 
de borde

\begin{equation}
  Z_{\mathrm{H}}(0) = 0
  \quad \mbox{y} \quad  
  Z_{\mathrm{H}}(r_{\mathrm{max}}) = q = 1
\end{equation}

In [9]:
# Defino la densidad SINGLE orbital
def densidad():
    noc = 1.0      # nro de ocupacion = 1 
    ang = 1.0/(4.0*pi)
    for i in range(nsize):
        den[i] = noc*(U[i,0]/r[i])**2*ang
    return den

In [10]:
# Defino el potencial de Hartree
# Uso el índice j (nro de iteracion) para no incluir el potencial Vh 
# en la primera iteración
def VHartree(j):
    if (j>0):
        # 1ra condicion de borde
        Up[0] = 0.0
        Zh[0] = 0.0
        Zh[1] = h
        for i in range(nsize):
            Upp[i] = -4.0*pi*den[i]*r[i]
        for i in range(nsize-1):
            Up[i+1] = Up[i] + 0.5*(Upp[i] + Upp[i+1])*h 
        # 2da condicion de borde
        alfa = -Up[nsize-1]
        for i in range(nsize-1):
            Zh[i+1] = Zh[i] + Up[i]*h + 0.5*Upp[i]*h**2 
        for i in range(nsize):
            Zh[i] = Zh[i] + alfa*r[i]
        for i in range(nsize):
            Vh[i] = Zh[i]/r[i]
    return Vh

In [11]:
# Inicializo algunas variables utiles en la iteración
# j : nro de iteraciones
j = 0
Eorb = []
u0 = zeros((nsize,1))

## Empieza loop

In [60]:
# Calculo la densidad y el potencial de Hartree
densidad()
VHartree(j)

# Construyo el operador T y el operador Vs (potencial efectivo)
T = (-0.5)*Laplacian(r)
Vs = -Z/r + l*(l+1)/(2*r**2) + Vh

In [61]:
# Construyo el Hamiltoniano del sistema
H =  T + diag(Vs)

In [62]:
# Calculo autovalores (E) y autovectores (U)
E,U = eigh(H)
j = j + 1

# Normalization
U = Normalizate(U,r)

In [63]:
# Corroboro normalización
suma = 0.0
for i in range(nsize):
    suma = suma + (U[i,0])**2
suma = suma*h
suma

0.99999999999999856

In [64]:
# Adjunto los resultados para ver los resultados de cada iteración
# Eorb : energías
# u0   : funciones radiales reducidas
Eorb.append(E[0])
Eorb

[-1.9999500024997479,
 -0.82066952676254057,
 -0.95084683845114115,
 -0.90868065262543418,
 -0.92067740231605744,
 -0.91712036536876596,
 -0.91816260292152996,
 -0.91785614868309506,
 -0.91794616441166299]

### El valor de la energía orbital 1s de HF es -0.917956

In [65]:
u0 = c_[u0,U[:,0]]
u0

array([[  0.00000000e+00,   2.80021427e-02,   2.21444657e-02, ...,
          2.35322980e-02,   2.35284207e-02,   2.35295599e-02],
       [  0.00000000e+00,   5.54470427e-02,   4.38491647e-02, ...,
          4.65970143e-02,   4.65893375e-02,   4.65915930e-02],
       [  0.00000000e+00,   8.23430168e-02,   6.51215547e-02, ...,
          6.92018281e-02,   6.91904288e-02,   6.91937780e-02],
       ..., 
       [  0.00000000e+00,   6.57646999e-09,   1.59278778e-06, ...,
          7.94231809e-07,   7.95913506e-07,   7.95419131e-07],
       [  0.00000000e+00,   4.38398456e-09,   1.06182664e-06, ...,
          5.29469824e-07,   5.30590924e-07,   5.30261350e-07],
       [  0.00000000e+00,   2.19189365e-09,   5.30903754e-07, ...,
          2.64729497e-07,   2.65290038e-07,   2.65125254e-07]])

## Termina loop

La energía total en este esquema está dada por:

\begin{equation}
E = \sum_i \epsilon_i - \int{dr \, V_{\mathrm{H}}^*(r) \, u_i^2(r) }
\end{equation}


In [66]:
# Calculo la integral del potencial Vh*
suma = 0.0
for i in range(nsize):
    suma = suma + Vh[i]*U[i,0]**2
Eh = suma*h
print(Eh)

1.02573319881


In [72]:
# Calculo la energia total del sistema
for i in range(j):
    if (i==0):
        Etot = 2.0*(Eorb[i])
    else:
        Etot = 2.0*(Eorb[i]) - Eh
    print('# de iteracion:',i,'  Etot = ',Etot)

# de iteracion: 0   Etot =  -3.999900005
# de iteracion: 1   Etot =  -2.66707225234
# de iteracion: 2   Etot =  -2.92742687571
# de iteracion: 3   Etot =  -2.84309450406
# de iteracion: 4   Etot =  -2.86708800344
# de iteracion: 5   Etot =  -2.85997392955
# de iteracion: 6   Etot =  -2.86205840465
# de iteracion: 7   Etot =  -2.86144549618
# de iteracion: 8   Etot =  -2.86162552763


### El valor de la energía total 1s^2 de HF es -2.861680